# 📈 W07 Lab: OpenSanctions Targets

**DS105A W07 LAB – Data for Data Science (Autumn Term 2025/2026)**

<div style="font-family: system-ui; padding: 20px 30px 20px 20px; background-color: #FFFFFF; color: #212121; border-left: 8px solid #47315E; border-radius: 8px; box-shadow: 0 4px 12px rgba(0, 0, 0, 0.1); max-width: 650px;">

**Purpose:** Rebuild the exact plot you saw at the start of the lab. The plotting code is ready; your job is to engineer the `plot_df` DataFrame that powers it.

<span style="display:block; line-height:1.2em; color:#555555; font-size:0.9em;">

**What you will practise**

 i) Inspecting nested OpenSanctions JSON exports
 ii) Using `pd.json_normalize()` to flatten targeted fields
 iii) Cleaning list-like columns without loops
 iv) Aggregating sanctions by authority ready for plotting

</span>

</div>


**⚙️ Library Imports**


In [ ]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
# import pycountry  # Uncomment in Part 3 when you want readable country names

sns.set_theme(style="whitegrid", context="talk")


## 🔁 Part 1: Understand the Finished Pipeline

Run the block below. We will inspect it together so you can see how each line helps transform the nested JSON into a tidy table. Keep the focus on how `pd.json_normalize()` and the follow-up cleaning steps work.


In [ ]:
# Load the 4,000-record OpenSanctions export (JSON lines format)
df_targets = pd.read_json('./data/opensanctions/targets_sample_4000.jsonl', lines=True)

# Focus on the nested fields we actually need inside the 'properties' column
interesting_columns = ['alias', 'nationality', 'birthCountry', 'sourceUrl', 'sanctions']
df_targets = pd.json_normalize(df_targets['properties'])[interesting_columns]

# Clean list-like columns and expand the sanctions list into one row per sanction
# - alias/sourceUrl/birthCountry arrive as single-item lists -> keep the first entry
# - nationality can have multiple entries -> join them into a readable string
# - explode('sanctions') gives us one sanction per row while duplicating the context columns
df_targets = (
    df_targets
    .assign(
        alias=lambda df: df['alias'].apply(lambda values: values[0] if isinstance(values, list) else None),
        sourceUrl=lambda df: df['sourceUrl'].apply(lambda values: values[0] if isinstance(values, list) else None),
        nationality=lambda df: df['nationality'].apply(lambda values: ', '.join(values) if isinstance(values, list) else None),
        birthCountry=lambda df: df['birthCountry'].apply(lambda values: values[0] if isinstance(values, list) else None)
    )
    .explode('sanctions')
)

# Pull the sanction country out of each nested sanction dictionary
sanction_country = pd.json_normalize(df_targets['sanctions'])['properties.country']
sanction_country = sanction_country.apply(lambda values: values[0] if isinstance(values, list) else None).tolist()
df_targets['sanction_country'] = sanction_country

# Remove the now-unpacked sanctions column
df_targets = df_targets.drop(columns='sanctions')

df_targets.head()


## 📊 Part 2: Build `plot_df` (40-50 min)

### Step 2.1: Create the aggregation

`plot_df` needs two columns, exactly in this order:

| column | description |
| --- | --- |
| `sanction_country` | ISO country code of the sanctioning authority |
| `num_targets` | Number of targets sanctioned by that country |

Use `df_targets` to engineer those values. You decide how much you filter or tidy (e.g. remove missing codes), but the final DataFrame must support the plotting code in the next cell.


In [ ]:
# TODO: create plot_df with columns ['sanction_country', 'num_targets']
# Remember: avoid for loops; chaining, groupby, value_counts, and list comprehensions are fine.

# plot_df = ...
# plot_df.head()


### Step 2.2: Create the plot

Once you have `plot_df`, run this code to create the visualisation:


In [ ]:
plt.figure(figsize=(10, 6))
sns.barplot(
    data=plot_df,
    x='num_targets',
    y='sanction_country',
    hue='num_targets',
    palette=sns.color_palette('Reds', n_colors=15),
    legend=False
)
plt.title('Most active sanctioning authorities in the sample')
plt.xlabel('Number of targets')
plt.ylabel('Sanction country (ISO code)')
plt.tight_layout()
plt.show()


### Step 2.3: (Optional) Embellish with readable country names

If you want to make the plot more readable, you can convert ISO codes to full country names:

1. Install `pycountry` if you have not already (`pip install pycountry`).
2. Uncomment the `pycountry` import at the top of the notebook.
3. Run the helper function below to convert ISO codes into readable country names.
4. Update your plot so the y-axis shows friendly labels instead of codes.


In [ ]:
# Remember to uncomment the `pycountry` import at the top before running this cell.

def get_nice_country_name(alpha_code):
    if not alpha_code or pd.isna(alpha_code):
        return None
    try:
        
        if alpha_code == 'eu':
            country_name = 'European Union'
        else:
            country = pycountry.countries.lookup(alpha_code)
            country_name = country.name
        return f"{country_name}".strip()
    except LookupError:
        return alpha_code



## ✍️ Part 3: Work on Mini Project 2 (0-10 min)

Has everyone started Mini Project 2 already? Look at the appendix in the project brief for tips on creating a tactical plan.

Use this time to:
- Review the Mini Project 2 requirements
- Ask TAs for help with any questions
- Start planning your approach

**Remember:** The skills you practised today (especially `pd.json_normalize()` and `.explode()`) will be essential for handling the TfL Journey Planner API responses in Mini Project 2.
